# LAMMPS Tutorials 01 nvt. Running your first LAMMPS simulation!

### Author: ABDELLAH TAHIRI 

Please contact me if you have a problem with this tutorial, so I can modify in Github.  I have added FAQs, and will update my versions of LAMMPS in the future to keep the scripts current.

The latest version of this [Jupyter Notebook](http://ipython.org/notebook.html) tutorial is available at https://github.com/athiri78/DM/edit/main/LAMMPS-Tutorials.



***

## Description:
<a id="Sec1"></a>

This script simulates the diffusion and reassembly of a 2D lattice that initially forms the "LM2A" logo. After an initial configuration step, the lattice is dissolved, and the velocities are reversed to allow the system to reassemble the logo. The simulation employs Lennard-Jones potentials to model interactions and uses a series of regions and blocks to create the letters and numbers of the logo in the 2D plane.

<img src="https://github.com/athiri78/-Molecular-Dynamics-simulations/blob/main/LMAA.gif" alt="LM2A" title="box" />

## Step 1: Download an Input File
<a id="Step1"></a>

This input script was run using the Aug 2024 version of LAMMPS. Changes in some commands may require revision of the input script. To get the input file, you have a few options:

*  Copy the text below and paste it into a text file, `lm2a.in`. Use the `Paste Special` command with unformatted text into the file. 
*  Or, I added the command `%%writefile lm2a.in` to the Jupyter Notebook which should just do everything for you!




In [8]:
%%writefile lm2a.in
#######################################################################
# PART A - ENERGY MINIMIZATION
#####################################################################
# Simulation of LMAA logo

units       lj
atom_style  atomic
dimension   2

# Create 2D lattice, low density so diffusion can occur
lattice     sq2 0.5 origin 0.25 0.25 0.0
region      box block 0 22 0 7 -0.5 0.5
create_box  2 box
create_atoms 1 box

# L for "L" letter
region      L1 block 2 3 1 6 -0.5 0.5
region      L2 block 2 5 1 2 -0.5 0.5
region      L union 2 L1 L2

# M for "M" letter
region      M1 block 6  7  1 6 -0.5 0.5
region      M2 block 10 11 1 6 -0.5 0.5
region      M3 block 6  11 5 6 -0.5 0.5
region      M4 block 8  9 3 6 -0.5 0.5
region      M union 4 M1 M2 M3 M4

#  "2" number 
region      A1 block 12 13 1 6 -0.5 0.5
region      A2 block 14 15 1 6 -0.5 0.5
region      A3 block 12 15 3 4 -0.5 0.5
region      A4 block 12 15 5 6 -0.5 0.5
region      A union 4 A1 A2 A3 A4

# Second A for "A" letter (modifying the position for the second 'A')
region      A5 block 16 17 1 6 -0.5 0.5
region      A6 block 18 19 1 6 -0.5 0.5
region      A7 block 16 19 3 4 -0.5 0.5
region      A8 block 16 19 5 6 -0.5 0.5
region      A2M union 4 A5 A6 A7 A8

# Combine all regions for LMAA
region      LMAA union 4 L M A A2M
set         region LMAA type 2

# LJ and other system parameters
mass        * 1.0
pair_style  lj/cut 2.5
pair_coeff  * * 1.0 1.0 2.5

# Simulation parameters
timestep    0.005
neighbor    0.3 bin
neigh_modify delay 0 every 1 check yes

velocity    all create 2.0 87287 loop geom

thermo      100
dump        1 all atom 20 lM2A.dump

# Run without integrator to "pause" the visualization
run         100

# Dissolve the lattice
fix         1 all nve
fix         2 all enforce2d
run         1000

# Run without integrator to "pause" the visualization
unfix       1
unfix       2
run         200

# Reverse the velocities and continue run
# Logo and lattice should reassemble within round-off errors
variable    vxflip atom -vx
variable    vyflip atom -vy
velocity    all set v_vxflip v_vyflip NULL

fix         1 all nve
fix         2 all enforce2d
run         1000

# Run without integrator to "pause" the visualization
unfix       1
unfix       2
run         100


print "All done!"

Writing lm2a.in


Awesome!  That little script should have written the above text to the file `nvt.in`.  To check, let's execute a command on the present directory listing all files that end in `*.in`.

In [10]:
!dir *.in

 Le volume dans le lecteur C n’a pas de nom.
 Le numéro de série du volume est DC02-C1A6

 Répertoire de C:\Users\pc\Desktop\M2A

21/11/2024  10:17             1 774 calc_fcc.in
12/11/2024  14:40             1 565 calc_fcc_ver1.in
09/11/2024  14:10             1 233 calc_fcc_ver2.in
23/12/2024  17:51             3 143 cylindre.in
23/12/2024  23:03             2 878 cylindre_LGV.in
27/02/2025  19:08             2 378 Diatomic.in
03/12/2024  12:22             1 113 Diatomic1.in
12/11/2024  16:49             1 177 lj.in
12/11/2024  17:08               533 ljbarosta.in
12/11/2024  17:19             1 389 ljovito.in
12/11/2024  18:10             1 018 ljrdf.in
12/11/2024  16:59               522 ljthermo.in
27/02/2025  19:09             2 378 lm2a.in
25/11/2024  12:17             2 875 minimization.in
25/11/2024  12:45             3 080 minimization1.in
03/12/2024  11:44             1 141 mixed.in
23/12/2024  23:18             1 373 molc.in
22/01/2025  16:16               752 nscf_si.in
26/

***
## Step 2: Running LAMMPS
### Run this using LAMMPS in Jupyter Notebook
We can actually run this from Jupyter Notebook.  Let's try it.

In [12]:
!lmp -in lm2a.in  -pk omp 8 -sf omp 

LAMMPS (29 Aug 2024 - Update 1)
OMP_NUM_THREADS environment is not set. Defaulting to 1 thread. (src/comm.cpp:98)
  using 1 OpenMP thread(s) per MPI task
Loaded 1 plugins from C:\LAMMPS 64-bit 29Aug2024\plugins
set 8 OpenMP thread(s) per MPI task
using multi-threaded neighbor list subroutines
Lattice spacing in x,y,z = 2 2 2
Created orthogonal box = (0 0 -1) to (44 14 1)
  1 by 1 by 1 MPI processor grid
Created 308 atoms
  using lattice units in orthogonal box = (0 0 -1) to (44 14 1)
  create_atoms CPU = 0.001 seconds
Setting atom values ...
  92 settings made for type
Generated 0 of 1 mixed pair_coeff terms from geometric mixing rule
Last active /omp style is pair_style lj/cut/omp
Neighbor list info ...
  update: every = 1 steps, delay = 0 steps, check = yes
  max neighbors/atom: 2000, page size: 100000
  master list distance cutoff = 2.8
  ghost atom cutoff = 2.8
  binsize = 1.4, bins = 32 10 2
  1 neighbor lists, perpetual/occasional/extra = 1 0 0
  (1) pair lj/cut/omp, perpetual
  

Sweet!

If you want to view the entire file (opening `log.lammps` in Notepad), then:

In [14]:
!type log.lammps

LAMMPS (29 Aug 2024 - Update 1)
OMP_NUM_THREADS environment is not set. Defaulting to 1 thread. (src/comm.cpp:98)
  using 1 OpenMP thread(s) per MPI task
Loaded 1 plugins from C:\LAMMPS 64-bit 29Aug2024\plugins
package omp 8
set 8 OpenMP thread(s) per MPI task
using multi-threaded neighbor list subroutines
#######################################################################
# PART A - ENERGY MINIMIZATION
#####################################################################
# Simulation of LMAA logo

units       lj
atom_style  atomic
dimension   2

# Create 2D lattice, low density so diffusion can occur
lattice     sq2 0.5 origin 0.25 0.25 0.0
Lattice spacing in x,y,z = 2 2 2
region      box block 0 22 0 7 -0.5 0.5
create_box  2 box
Created orthogonal box = (0 0 -1) to (44 14 1)
  1 by 1 by 1 MPI processor grid
create_atoms 1 box
Created 308 atoms
  using lattice units in orthogonal box = (0 0 -1) to (44 14 1)
  create_atoms CPU = 0.001 seconds

# L for "L" letter
region      L1 bloc

In [24]:
!type dump.lammpstrj


ITEM: TIMESTEP
400
ITEM: NUMBER OF ATOMS
1600
ITEM: BOX BOUNDS pp pp pp
-2.0000000000000000e+01 2.0000000000000000e+01
-2.0000000000000000e+01 2.0000000000000000e+01
-2.0000000000000000e+01 2.0000000000000000e+01
ITEM: ATOMS id type xs ys zs
1363 1 0.0147887 0.00484529 0.00330571
1212 1 0.613732 0.00517243 0.0107883
1001 1 0.525885 0.0614909 0.0159888
23 1 0.0724548 0.0838375 0.0309441
436 1 0.503659 0.0787331 0.0171671
497 1 0.367847 0.110011 0.00896643
412 1 0.425477 0.129418 0.029216
100 1 0.169811 0.168548 0.0154248
1015 1 0.568998 0.164363 0.00444204
279 1 0.811356 0.204889 0.011357
111 1 0.169658 0.237981 0.0150673
697 1 0.971789 0.226193 0.00704059
5 1 0.627416 0.250815 0.00671556
763 1 0.629386 0.279891 0.00856858
1407 1 0.815466 0.272469 0.0108513
408 1 0.861706 0.296335 0.0301302
617 1 0.88096 0.31927 0.0289331
1234 1 0.0405067 0.346158 0.0270539
274 1 0.0692618 0.351872 0.0273548
456 1 0.0555011 0.347074 0.00291775
1009 1 0.0304868 0.358207 0.005036
312 1 0.0327884 0.386918 

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



***
## FAQs 
<br>
<div class="alert alert-danger">
<strong>Question 1</strong>: Write a LAMMPS script to visualize your name
</div>


***
## Tutorial Links

[Click here to open the next tutorial](LAMMPS-Tutorials-02.ipynb)